**Importing libraries and method**
***
In this step I will use knn to calculate color palettes providing knn all the colors in the image and letting it cluster them into 5 groups, then I extract the centroids.

In [1]:
from skimage.io import imread
import skimage.transform as st
from sklearn.cluster import KMeans
from IPython.display import clear_output

import warnings
warnings.filterwarnings('ignore')


import os
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
%matplotlib inline


**Main functions**

In [2]:
# Function to get the palette for one image
def get_pallete(image_filename, k=5, target_size = 240):
    
    image = np.array(imread(image_filename), dtype=np.float64) / 255
    w, h, d  = image.shape
    if w>h:
        ratio = target_size/h
    else:
        ratio = target_size/w

    image = st.rescale(image, ratio, channel_axis=2)

    w, h, d  = image.shape
    image = np.reshape(image, (w * h, d))
    
    clf = KMeans(n_clusters=k)
    clf.fit(image)
    return clf.cluster_centers_

In [157]:
# simple function to plot the palette as a row of 5 squares of color
def plot_pallete(nodes):
    
    fig,ax = plt.subplots(1,1,figsize=(8,2))
    ax.imshow(nodes.reshape(1,len(nodes),3), interpolation='nearest')
    ax.xaxis.set_visible(False)
    ax.yaxis.set_visible(False)

In [38]:
# Loading the museum art pieces to cluster them
data_museum = pd.read_csv("CSV's/artic_edu_Valid_paintings.csv")

In [59]:
# This function picks a dataset and returns a new dataset with all the images clustered
def get_pallete_df(sub_path, ids, file_type=''):
    # empty list and dataframe to accomodate results.
    lst = []
    palete_df = pd.DataFrame(columns = ['c1_r', 'c1_g', 'c1_b','c2_r', 'c2_g', 'c2_b','c3_r', 'c3_g', 'c3_b',
                                       'c4_r', 'c4_g', 'c4_b','c5_r', 'c5_g', 'c5_b', 'id'])

    #control flags and variables the keep trak on progress
    remaining = len(ids)
    flag = 0

    for i in ids:
        try:
            path = sub_path+i+file_type
            centroids = list(get_pallete(path))
            centroids.append([i])
            palete_df.loc[len(palete_df)] = [item for sublist in centroids for item in sublist]
            print(i,'added', remaining-flag,'items pending')
        except:
            print(i, "cant be processed")       
        flag +=1
        
    return palete_df
    

In [210]:
def merge_df(merge):
    
    # Droping potencial rows with nan's (corrupt files) and possible duplicates
    merge.drop_duplicates(subset=['id'])
    merge = merge.dropna(subset=['c1_r'])
    
    # creating columns for color tuples
    merge['rgb_1'] = list(zip(round(merge.c1_r*255), round(merge.c1_g*255), round(merge.c1_b*255)))
    merge['rgb_2'] = list(zip(round(merge.c2_r*255), round(merge.c2_g*255), round(merge.c2_b*255)))
    merge['rgb_3'] = list(zip(round(merge.c3_r*255), round(merge.c3_g*255), round(merge.c3_b*255)))
    merge['rgb_4'] = list(zip(round(merge.c4_r*255), round(merge.c4_g*255), round(merge.c4_b*255)))
    merge['rgb_5'] = list(zip(round(merge.c5_r*255), round(merge.c5_g*255), round(merge.c5_b*255)))

    # creating average colors
    merge['avg_r'] = round(((merge.c1_r+merge.c2_r+merge.c3_r+merge.c4_r+merge.c5_r)/5)*255)
    merge['avg_g'] = round(((merge.c1_g+merge.c2_g+merge.c3_g+merge.c4_g+merge.c5_g)/5)*255)
    merge['avg_b'] = round(((merge.c1_b+merge.c2_b+merge.c3_b+merge.c4_b+merge.c5_b)/5)*255)

#     calculating the average colors
    merge['avg_color'] = list(zip(round(((merge.c1_r+merge.c2_r+merge.c3_r+merge.c4_r+merge.c5_r)/5)*255),round(((merge.c1_g+merge.c2_g+merge.c3_g+merge.c4_g+merge.c5_g)/5)*255),round(((merge.c1_b+merge.c2_b+merge.c3_b+merge.c4_b+merge.c5_b)/5)*255)))   

    # tuples to list
    merge.rgb_1 = [list(x) for x in merge.rgb_1]
    merge.rgb_2 = [list(x) for x in merge.rgb_2]
    merge.rgb_3 = [list(x) for x in merge.rgb_3]
    merge.rgb_4 = [list(x) for x in merge.rgb_4]
    merge.rgb_5 = [list(x) for x in merge.rgb_5]
    
    return merge

In [ ]:
# getting relative workpaths for chicago museum and clustering
work_path = os.getcwd() +'/Images/images_chicago/'
chicago_df = get_pallete_df(work_path, data_museum.image_id, '.jpg')

In [7]:
data_museum = data_museum[['date_start', 'artist_display','style_title', 'artist_title', 'image_id', 'title',
       'publication_history']]

data_museum.columns = ['year', 'small_bio', 'style', 'artiste','id', 'title', 'publication_history']
merge = data_museum.merge(palete_df, on='id', how='right')

In [34]:
merge = merge_df(merge)

c1_r      c1_g      c1_b      c2_r      c2_g      c2_b      c3_r  \
0     0.675297  0.542384  0.408268  0.477338  0.482700  0.421463  0.299851   
1     0.319773  0.383594  0.318466  0.552279  0.593119  0.568339  0.533336   
2     0.530392  0.538601  0.643541  0.677863  0.685382  0.775079  0.622054   
3     0.360716  0.345150  0.334518  0.873524  0.843922  0.790979  0.638892   
4     0.654724  0.706967  0.749097  0.441853  0.481301  0.477897  0.548538   
...        ...       ...       ...       ...       ...       ...       ...   
1479  0.150863  0.131768  0.089021  0.742721  0.598897  0.331666  0.008826   
1480  0.219971  0.248647  0.189532  0.528748  0.487225  0.348594  0.131751   
1481  0.719233  0.659838  0.479665  0.629917  0.540893  0.354676  0.364529   
1482  0.434822  0.380385  0.315100  0.218682  0.177224  0.139430  0.671227   
1483  0.067475  0.067475  0.067475  0.130844  0.130844  0.130844  0.209627   

          c3_g      c3_b      c4_r      c4_g      c4_b      c5_r      c5_g  \
0     0.433810  0.508885  0.541464  0.626463  0.638488  0.322627  0.394819   
1     0.534608  0.394929  0.671043  0.654960  0.582450  0.407706  0.457314   
2     0.618746  0.706719  0.731521  0.689999  0.713697  0.444741  0.467477   
3     0.576125  0.487791  0.513535  0.462137  0.394302  0.755240  0.703947   
4     0.594579  0.613860  0.384348  0.385085  0.349139  0.744032  0.792030   
...        ...       ...       ...       ...       ...       ...       ...   
1479  0.018289  0.011615  0.512608  0.395758  0.237527  0.269423  0.245766   
1480  0.132206  0.111348  0.335680  0.356912  0.270427  0.821077  0.692954   
1481  0.353666  0.252998  0.849368  0.835368  0.740351  0.794704  0.739778   
1482  0.570837  0.484357  0.320777  0.277440  0.225095  0.406887  0.206824   
1483  0.209627  0.209627  0.541343  0.541343  0.541343  0.329642  0.329642   

          c5_b  
0     0.365084  
1     0.359893  
2     0.556649  
3     0.623371  
4     0.828221  
...        ...  
1479  0.199563  
1480  0.533354  
1481  0.576056  
1482  0.125818  
1483  0.329642  

[1484 rows x 15 columns]

In [36]:
merge.to_csv("CSV's/artic_edu_Valid_paintings_pallete.csv")

**Calculating color palletes for test and train sets**

In [39]:
data = pd.read_csv("CSV's/Treated_artist_by_movement_paintings.csv")

In [43]:
data = data[['date', 'artist', 'style', 'new_filename', 'in_train']]

In [45]:
data.columns = ['year', 'artiste', 'style', 'id', 'in_train']

In [46]:
data_train = data[data.in_train == True]
data_test = data[data.in_train == False]

In [60]:
train_pallete = get_pallete_df("E:/train/", data_train.id)
test_pallete = get_pallete_df("E:/test/", data_test.id)

102257.jpg added 79375 items pending
102257.jpg added 79374 items pending
75232.jpg added 79373 items pending
75232.jpg added 79372 items pending
29855.jpg added 79371 items pending
62252.jpg added 79370 items pending
62252.jpg added 79369 items pending
63861.jpg added 79368 items pending
63861.jpg added 79367 items pending
53180.jpg added 79366 items pending
70944.jpg added 79365 items pending
59792.jpg added 79364 items pending
48138.jpg added 79363 items pending
99442.jpg added 79362 items pending
23508.jpg added 79361 items pending
82352.jpg added 79360 items pending
27254.jpg added 79359 items pending
47145.jpg added 79358 items pending
59145.jpg added 79357 items pending
59145.jpg added 79356 items pending
16876.jpg added 79355 items pending
28908.jpg added 79354 items pending
48177.jpg added 79353 items pending
7486.jpg added 79352 items pending
35766.jpg added 79351 items pending
28363.jpg added 79350 items pending
71024.jpg added 79349 items pending
70728.jpg added 79348 items

73923.jpg added 79146 items pending
82310.jpg added 79145 items pending
69300.jpg added 79144 items pending
61125.jpg added 79143 items pending
97348.jpg added 79142 items pending
39533.jpg added 79141 items pending
34850.jpg added 79140 items pending
95359.jpg added 79139 items pending
5241.jpg added 79138 items pending
62271.jpg added 79137 items pending
65103.jpg added 79136 items pending
25503.jpg added 79135 items pending
89279.jpg added 79134 items pending
76728.jpg added 79133 items pending
55948.jpg added 79132 items pending
87503.jpg added 79131 items pending
8362.jpg added 79130 items pending
12836.jpg added 79129 items pending
60761.jpg added 79128 items pending
32721.jpg added 79127 items pending
9348.jpg added 79126 items pending
75013.jpg added 79125 items pending
25251.jpg added 79124 items pending
29391.jpg added 79123 items pending
8943.jpg added 79122 items pending
80078.jpg added 79121 items pending
86506.jpg added 79120 items pending
19281.jpg added 79119 items pend

9158.jpg added 78917 items pending
23452.jpg added 78916 items pending
72942.jpg added 78915 items pending
63564.jpg added 78914 items pending
42954.jpg added 78913 items pending
12155.jpg added 78912 items pending
42432.jpg added 78911 items pending
88767.jpg added 78910 items pending
76388.jpg added 78909 items pending
82140.jpg added 78908 items pending
39586.jpg added 78907 items pending
83092.jpg added 78906 items pending
50272.jpg added 78905 items pending
13889.jpg added 78904 items pending
75187.jpg added 78903 items pending
55979.jpg added 78902 items pending
39086.jpg added 78901 items pending
58564.jpg added 78900 items pending
28179.jpg added 78899 items pending
48736.jpg added 78898 items pending
76577.jpg added 78897 items pending
2918.jpg added 78896 items pending
44603.jpg added 78895 items pending
42415.jpg added 78894 items pending
28187.jpg added 78893 items pending
47417.jpg added 78892 items pending
74498.jpg added 78891 items pending
84023.jpg added 78890 items pe

58752.jpg added 78687 items pending
92783.jpg added 78686 items pending
28838.jpg added 78685 items pending
59656.jpg added 78684 items pending
73974.jpg added 78683 items pending
41490.jpg added 78682 items pending
41490.jpg added 78681 items pending
7325.jpg added 78680 items pending
79303.jpg added 78679 items pending
93259.jpg added 78678 items pending
36741.jpg added 78677 items pending
90528.jpg added 78676 items pending
6821.jpg added 78675 items pending
19865.jpg added 78674 items pending
11195.jpg added 78673 items pending
16725.jpg added 78672 items pending
12999.jpg added 78671 items pending
47115.jpg added 78670 items pending
21931.jpg added 78669 items pending
34053.jpg added 78668 items pending
32899.jpg added 78667 items pending
83949.jpg added 78666 items pending
88641.jpg added 78665 items pending
54359.jpg added 78664 items pending
81691.jpg added 78663 items pending
50050.jpg added 78662 items pending
59772.jpg added 78661 items pending
33627.jpg added 78660 items pe

27489.jpg added 78458 items pending
84942.jpg added 78457 items pending
14201.jpg added 78456 items pending
17296.jpg added 78455 items pending
84765.jpg added 78454 items pending
87207.jpg added 78453 items pending
62024.jpg added 78452 items pending
36402.jpg added 78451 items pending
99133.jpg added 78450 items pending
94129.jpg added 78449 items pending
52238.jpg added 78448 items pending
30586.jpg added 78447 items pending
91694.jpg added 78446 items pending
1695.jpg added 78445 items pending
72449.jpg added 78444 items pending
101370.jpg added 78443 items pending
96931.jpg added 78442 items pending
43341.jpg added 78441 items pending
40252.jpg added 78440 items pending
79816.jpg added 78439 items pending
26501.jpg added 78438 items pending
65732.jpg added 78437 items pending
45572.jpg added 78436 items pending
58880.jpg added 78435 items pending
56587.jpg added 78434 items pending
28824.jpg added 78433 items pending
43585.jpg added 78432 items pending
85895.jpg added 78431 items 

...

11553.jpg cant be processed
48495.jpg cant be processed
46928.jpg cant be processed
90926.jpg cant be processed
94948.jpg cant be processed
21880.jpg cant be processed
88531.jpg cant be processed
71127.jpg cant be processed
101167.jpg cant be processed
49438.jpg cant be processed
62659.jpg cant be processed
65139.jpg cant be processed
5392.jpg cant be processed
49043.jpg cant be processed
10052.jpg cant be processed
74558.jpg cant be processed
84629.jpg cant be processed
86717.jpg cant be processed
28704.jpg cant be processed
75744.jpg cant be processed
75036.jpg cant be processed
13831.jpg cant be processed
15359.jpg cant be processed
24554.jpg cant be processed
23978.jpg cant be processed
86876.jpg cant be processed
73296.jpg cant be processed
79660.jpg cant be processed
61216.jpg cant be processed
68328.jpg cant be processed
15757.jpg cant be processed
62764.jpg cant be processed
30213.jpg cant be processed
23101.jpg cant be processed
92415.jpg cant be processed
1602.jpg cant be pro

7154.jpg cant be processed
41485.jpg cant be processed
522.jpg cant be processed
3884.jpg cant be processed
45310.jpg cant be processed
8315.jpg cant be processed
82561.jpg cant be processed
39759.jpg cant be processed
32744.jpg cant be processed
88336.jpg cant be processed
73966.jpg cant be processed
79347.jpg cant be processed
49727.jpg cant be processed
39316.jpg cant be processed
47807.jpg cant be processed
33560.jpg cant be processed
33560.jpg cant be processed
48981.jpg cant be processed
53389.jpg cant be processed
41355.jpg cant be processed
8703.jpg cant be processed
93232.jpg cant be processed
20960.jpg cant be processed
91869.jpg cant be processed
74629.jpg cant be processed
97411.jpg cant be processed
40845.jpg cant be processed
65588.jpg cant be processed
65588.jpg cant be processed
62410.jpg cant be processed
81086.jpg cant be processed
66053.jpg cant be processed
96330.jpg cant be processed
61374.jpg cant be processed
28799.jpg cant be processed
47678.jpg cant be processe

74974.jpg cant be processed
53467.jpg cant be processed
82605.jpg cant be processed
35535.jpg cant be processed
3739.jpg cant be processed
84162.jpg cant be processed
49194.jpg cant be processed
5906.jpg cant be processed
21887.jpg cant be processed
37667.jpg cant be processed
35702.jpg cant be processed
46626.jpg cant be processed
12792.jpg cant be processed
44539.jpg cant be processed
12439.jpg cant be processed
39426.jpg cant be processed
102299.jpg cant be processed
69175.jpg cant be processed
67118.jpg cant be processed
15651.jpg cant be processed
86008.jpg cant be processed
71880.jpg cant be processed
62029.jpg cant be processed
94472.jpg cant be processed
24024.jpg cant be processed
5229.jpg cant be processed
89708.jpg cant be processed
54324.jpg cant be processed
88686.jpg cant be processed
90208.jpg cant be processed
88417.jpg cant be processed
65911.jpg cant be processed
83548.jpg cant be processed
71947.jpg cant be processed
43643.jpg cant be processed
39207.jpg cant be proc

46360.jpg cant be processed
40321.jpg cant be processed
92061.jpg cant be processed
33218.jpg cant be processed
99331.jpg cant be processed
13646.jpg cant be processed
24660.jpg cant be processed
19730.jpg cant be processed
13046.jpg cant be processed
6292.jpg cant be processed
18843.jpg cant be processed
58186.jpg cant be processed
89405.jpg cant be processed
97201.jpg cant be processed
48792.jpg cant be processed
43906.jpg cant be processed
57860.jpg cant be processed
40894.jpg cant be processed
39919.jpg cant be processed
29394.jpg cant be processed
13553.jpg cant be processed
75409.jpg cant be processed
32682.jpg cant be processed
12600.jpg cant be processed
96813.jpg cant be processed
7627.jpg cant be processed
102922.jpg cant be processed
86562.jpg cant be processed
102568.jpg cant be processed
42096.jpg cant be processed
82483.jpg cant be processed
13345.jpg cant be processed
64713.jpg cant be processed
49878.jpg cant be processed
43075.jpg cant be processed
98979.jpg cant be pr

89946.jpg cant be processed
92365.jpg cant be processed
24961.jpg cant be processed
3956.jpg cant be processed
25244.jpg cant be processed
73184.jpg cant be processed
80119.jpg cant be processed
3186.jpg cant be processed
54741.jpg cant be processed
28834.jpg cant be processed
38823.jpg cant be processed
25779.jpg cant be processed
90937.jpg cant be processed
53504.jpg cant be processed
21361.jpg cant be processed
24462.jpg cant be processed
69126.jpg cant be processed
71645.jpg cant be processed
24223.jpg cant be processed
61129.jpg cant be processed
79330.jpg cant be processed
22795.jpg cant be processed
84829.jpg cant be processed
85439.jpg cant be processed
17293.jpg cant be processed
94045.jpg cant be processed
94615.jpg cant be processed
68494.jpg cant be processed
55379.jpg cant be processed
31746.jpg cant be processed
101826.jpg cant be processed
50120.jpg cant be processed
51870.jpg cant be processed
81006.jpg cant be processed
59945.jpg cant be processed
13996.jpg cant be pro

In [118]:
# merging the colors with the train dataset
merge = data_train.merge(train_pallete, on='id', how='left')
merge = merge_df(merge)

In [205]:
merge.to_csv("CSV's/trainset_color_palletes.csv")

**Only did the train set, but the test is the exact same**